##  Proyecto 1:
### *Data Profiling* y Mapas:

**Cargando librerías:**

In [104]:
#%load_ext pycodestyle_magic
#%pycodestyle_on

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import re
import datetime
import numpy as np
import folium
from matplotlib.ticker import FuncFormatter

In [105]:
#define categorical, numerical and date columns
CAT_COLS = ["dia_semana", "codigo_cierre", "año_cierre", "mes_cierre", "mes", "delegacion_inicio", 
            "incidente_c4", "clas_con_f_alarma", "tipo_entrada", "delegacion_cierre", "hora_creacion",
           "hora_cierre"]

DATE_COLS = ["fecha_creacion", "fecha_cierre"]

NUM_COLS = ["latitud", "longitud"]

In [106]:
#esto irá en el script ingestion .py
def ingest_file(file_name):
    """
    Function to retrieve and return the accidents dataset.
    Parameters:
    -----------
    file_name: str
               Path to the file.
    Returns:
    --------
    df: pandas dataframe
    """
    df = pd.read_csv(file_name)
    return df


def drop_cols(df):
    """
    Function to drop unnnecesary columns in the dataset.
    """
    df.drop(columns = ['folio', 'geopoint', 'mes', 'mes_cierre', 'hora_cierre', 'año_cierre'], inplace = True)
    return df



def fill_na(df):
    """
    Function to fill null values in a dataframe.
    """
    #aquí podemos ir agregando más cosas cuando descubramos 
    #cómo imputar valores faltantes para latitud y longitud
    df.fillna({
        'delegacion_inicio': 'No Disponible',
        'delegacion_cierre': 'No Disponible'
              }, inplace = True)
    return df


def categoric_transformation(col,df):
    df[col] = df[col].astype("category")
    return df 

def create_categorical(cols, df):
    """
    Function to transform and prepare the categorical features in the dataset.
    """
    #transform to appropriate data type
    for col in cols: 
        df = categoric_transformation(col, df)
     
    return df


def date_transformation(col,df):
    """
    Function to prepare and transform date-type columns. 
    """
    df[col] = pd.to_datetime(df[col], dayfirst = True)
    return df

def create_date_cols(cols, df):
    for col in cols:
        df = date_transformation(col, df)
    return df 



def generate_label(df):
    """
    Function to create a new column indicating whether there was
    a false alarm or not. 
    Parameters:
    -----------
    df: pandas dataframe
    
    Returns:
    --------
    df: pandas dataframe
    """
    #transformamos la columna para solo quedarnos con la letra del código
    df["codigo_cierre"] = df["codigo_cierre"].apply(lambda x: x[1])
    df['label'] = np.where(
        (df.codigo_cierre == 'F') | (df.codigo_cierre == 'N'), 1, 0)
    return df 


def clean_hora_creacion(df):
    """
    Function to transform hours with incorrect format to timedelta format. 
    """
    horas_raw = df.hora_creacion.values.tolist()
    horas_clean = [datetime.timedelta(days=float(e)) if e.startswith("0.") else e for e in horas_raw]
    df["hora_creacion"] = horas_clean
    return df 


def create_simple_hour(df):
    """
    Function to extract the hour from the column "hora_creacion"
    Parameters:
    -----------
    df: pandas dataframe
    
    Returns:
    ---------
    df: pandas dataframe with a new column indicating the hour. 
    """
    #la función se podria adaptar para devolver minuto o segundo pero no lo considero necesario
    pattern = '\d+' #encuentra uno o más dígitos
    horas_raw = df.hora_creacion.astype(str).values #son así: '22:35:04', '22:50:49', '09:40:11'
    n = len(horas_raw)
    horas_clean = [0]*n #es más rápido reasignar valores que hacer .append()
    for i in range(n):
        hora_raw = horas_raw[i]
        hora_clean = re.match(pattern, hora_raw)[0] #solo queremos la hora, esto devuelve un objeto
        horas_clean[i] = hora_clean
    
    df["hora_simple"] = horas_clean
    return df 


def add_date_columns(df):
    """
    Esta función es muy importante puesto que nos ayudará a crear el mes, día y año de creación
    del registro. De esta manera podemos prescindir de las fechas de cierre, que no tendríamos en tiempo
    real en un modelo. 
    Parameters:
    -----------
    df: pandas dataframe
    
    Returns:
    ---------
    df: pandas dataframe with 4 new columns
    """
    mapping_meses = {1: "Enero", 2: "Febrero", 3: "Marzo", 4: "Abril", 5: "Mayo",
                       6: "Junio", 7: "Julio", 8: "Agosto", 9: "Septiembre", 10: "Octubre",
                       11: "Noviembre", 12: "Diciembre"}
    
    
    df["año_creacion"] = df.fecha_creacion.dt.year
    df["mes_creacion"] = df.fecha_creacion.dt.month
    df["dia_creacion"] = df.fecha_creacion.dt.day
    df["mes_creacion_str"] = df.mes_creacion.map(mapping_meses)
    df["año_creacion"] = df["año_creacion"].astype(str)
    return df 


def create_time_blocks(df):
    """
    Function to group the hour of the day into 3-hour blocks.
    Parameters:
    -----------
    df: pandas dataframe
    
    Returns:
    ---------
    df: pandas dataframe with a new column indicating the time-block.
    """
    horas_int = set(df.hora_simple.astype(int).values) #estaba como categórico
    f = lambda x: 12 if x == 0 else x
    mapping_hours = {}
    for hora in horas_int:
        grupo = (hora // 3) * 3
        if grupo < 12: 
            nombre_grupo = str(f(grupo)) + "-" + str(grupo + 2) + " a.m."
        else:
            hora_tarde = grupo % 12
            nombre_grupo = str(f(hora_tarde)) + "-" + str(hora_tarde + 2) + " p.m."
        mapping_hours[hora] = nombre_grupo
    
    df["espacio_del_dia"] = df["hora_simple"].astype(int).map(mapping_hours)
    return df
    

    

    
def basic_preprocessing(path):
    """
    Function to summarize all the preprocessing done to the data.
    Parameters:
    -----------
    path: str
          Path to your file
    
    Returns:
    ---------
    df: pandas dataframe
    """
    df = ingest_file(path) 
    df = generate_label(df)
    df = fill_na(df) 
    df = clean_hora_creacion(df)
    df = create_categorical(CAT_COLS, df) #transform to appropriate data types
    df = create_date_cols(DATE_COLS, df)
    df = add_date_columns(df)
    df = create_simple_hour(df)
    df = create_time_blocks(df)
    df = drop_cols(df)
    
    return df

**Cargando archivo y haciendo pre-procesamiento:**

In [107]:
data = basic_preprocessing('/Users/Leo/Documents/MCD/1o/IDS/Proyectos/proyecto1/datos/incidentes-viales-c5.csv')
data.head()

fecha_creacion hora_creacion dia_semana codigo_cierre fecha_cierre  \
0     2016-01-23      22:35:04     Sábado             A   2016-01-24   
1     2016-01-23      22:50:49     Sábado             A   2016-01-24   
2     2016-01-24      09:40:11    Domingo             N   2016-01-24   
3     2016-01-24      22:40:57    Domingo             N   2016-01-24   
4     2016-01-24      04:25:15    Domingo             A   2016-01-24   

     delegacion_inicio                     incidente_c4    latitud   longitud  \
0  VENUSTIANO CARRANZA  accidente-choque sin lesionados  19.422113 -99.084643   
1           CUAJIMALPA  accidente-choque con lesionados  19.358320 -99.297641   
2              TLALPAN  accidente-choque sin lesionados  19.217070 -99.219070   
3  MAGDALENA CONTRERAS  accidente-choque sin lesionados  19.320580 -99.241010   
4       MIGUEL HIDALGO  accidente-choque sin lesionados  19.452900 -99.215870   

   clas_con_f_alarma      tipo_entrada    delegacion_cierre  label  \
0         EMERGENCIA  BOTÓN DE AUXILIO  VENUSTIANO CARRANZA      0   
1  URGENCIAS MEDICAS  BOTÓN DE AUXILIO           CUAJIMALPA      0   
2         EMERGENCIA   LLAMADA DEL 066              TLALPAN      1   
3         EMERGENCIA   LLAMADA DEL 066  MAGDALENA CONTRERAS      1   
4         EMERGENCIA   LLAMADA DEL 066       MIGUEL HIDALGO      0   

  año_creacion  mes_creacion  dia_creacion mes_creacion_str hora_simple  \
0         2016             1            23            Enero          22   
1         2016             1            23            Enero          22   
2         2016             1            24            Enero          09   
3         2016             1            24            Enero          22   
4         2016             1            24            Enero          04   

  espacio_del_dia  
0       9-11 p.m.  
1       9-11 p.m.  
2       9-11 a.m.  
3       9-11 p.m.  
4        3-5 a.m.

In [108]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1383138 entries, 0 to 1383137
Data columns (total 19 columns):
 #   Column             Non-Null Count    Dtype         
---  ------             --------------    -----         
 0   fecha_creacion     1383138 non-null  datetime64[ns]
 1   hora_creacion      1383138 non-null  category      
 2   dia_semana         1383138 non-null  category      
 3   codigo_cierre      1383138 non-null  category      
 4   fecha_cierre       1383138 non-null  datetime64[ns]
 5   delegacion_inicio  1383138 non-null  category      
 6   incidente_c4       1383138 non-null  category      
 7   latitud            1382695 non-null  float64       
 8   longitud           1382703 non-null  float64       
 9   clas_con_f_alarma  1383138 non-null  category      
 10  tipo_entrada       1383138 non-null  category      
 11  delegacion_cierre  1383138 non-null  category      
 12  label              1383138 non-null  int64         
 13  año_creacion       1383138 

## Cambiando a categóricas las variables necesarias:

In [109]:
for col in ["año_creacion", "mes_creacion", "dia_creacion", "mes_creacion_str", "hora_simple", "espacio_del_dia"]:
    data[col] = data[col].astype("category")

In [110]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1383138 entries, 0 to 1383137
Data columns (total 19 columns):
 #   Column             Non-Null Count    Dtype         
---  ------             --------------    -----         
 0   fecha_creacion     1383138 non-null  datetime64[ns]
 1   hora_creacion      1383138 non-null  category      
 2   dia_semana         1383138 non-null  category      
 3   codigo_cierre      1383138 non-null  category      
 4   fecha_cierre       1383138 non-null  datetime64[ns]
 5   delegacion_inicio  1383138 non-null  category      
 6   incidente_c4       1383138 non-null  category      
 7   latitud            1382695 non-null  float64       
 8   longitud           1382703 non-null  float64       
 9   clas_con_f_alarma  1383138 non-null  category      
 10  tipo_entrada       1383138 non-null  category      
 11  delegacion_cierre  1383138 non-null  category      
 12  label              1383138 non-null  int64         
 13  año_creacion       1383138 

### Tablas de *data profiling*:

El *data profiling* se realizará sobre la información final, sobre la que estaremos trabajando durante el resto del proyecto.

**Nota:**  Éste *data profiling* se realiza sobre la totalidad de las llamadas, con etiqueta `0` y etiqueta `1`.  El desglose más detallado por etiquetas se aprecia con mayor claridad en el **GEDA**.

In [111]:
# Definiendo columnas numéricas:
number_variables = data.select_dtypes(include = 'int64').columns.values
(len(number_variables), number_variables)

(1, array(['label'], dtype=object))

In [112]:
# Definiendo columnas categóricas:
category_variables = data.select_dtypes(include = 'category').columns.values
(len(category_variables), category_variables)

(14,
 array(['hora_creacion', 'dia_semana', 'codigo_cierre',
        'delegacion_inicio', 'incidente_c4', 'clas_con_f_alarma',
        'tipo_entrada', 'delegacion_cierre', 'año_creacion',
        'mes_creacion', 'dia_creacion', 'mes_creacion_str', 'hora_simple',
        'espacio_del_dia'], dtype=object))

In [113]:
# Definiendo columnas de fecha:
date_variables = data.select_dtypes(include = 'datetime').columns.values
(len(date_variables), date_variables)

(2, array(['fecha_creacion', 'fecha_cierre'], dtype=object))

In [114]:
# Definiendo columnas geoespaciales:
geospace_variables = data.select_dtypes(include = 'float64').columns.values
(len(geospace_variables), geospace_variables)

(2, array(['latitud', 'longitud'], dtype=object))

In [115]:
# Verificando si tenemos todas las columnas:
if (sum([len(number_variables), len(category_variables), 
      len(date_variables), len(geospace_variables)]) == data.shape[1]): 
    print('OK')
else:
    print('Columns missing')

OK


***Data profiling* de variables numéricas:**

In [116]:
def get_repeated_values(df, col, top):
    top_5 = df.groupby([col])[col]\
                    .count()\
                    .sort_values(ascending = False)\
                    .head(3)
    indexes_top_5 = top_5.index
    
    if ((top == 1) and (len(indexes_top_5) > 0)):
        return indexes_top_5[0]
    elif ((top == 2) and (len(indexes_top_5) > 1)):
        return indexes_top_5[1]
    elif ((top == 3) and (len(indexes_top_5) > 2)):
        return indexes_top_5[2]
    else: 
        return 'undefined'

In [117]:
def numeric_profiling(df, col):
    """
    Profiling for numeric columns. 
    
    :param: column to analyze
    :return: dictionary
    """
    profiling = {}

    profiling.update({'max': df[col].max(),
                     'min': df[col].min(),
                     'mean': df[col].mean(),
                     'stdv': df[col].std(),
                     '25%': df[col].quantile(.25),
                     'median': df[col].median(),
                     '75%': df[col].quantile(.75),
                     'kurtosis': df[col].kurt(),
                     'skewness': df[col].skew(),
                     'uniques': df[col].nunique(),
                     'prop_missings': df[col].isna().sum()/df.shape[0]*100,
                     'top1_repeated': get_repeated_values(df, col, 1),
                     'top2_repeated': get_repeated_values(df, col, 2),})
    
    return profiling

In [118]:
profiling_dict = {}

numeric_profiling_output = {elem: numeric_profiling(data, elem)\
                            for elem in number_variables}

In [119]:
df_numeric_profiling = pd.DataFrame(numeric_profiling_output).reset_index()
df_numeric_profiling.rename(columns={'index': 'metric'}, inplace=True)
df_numeric_profiling

metric     label
0             25%  0.000000
1             75%  0.000000
2        kurtosis  0.155930
3             max  1.000000
4            mean  0.204103
5          median  0.000000
6             min  0.000000
7   prop_missings  0.000000
8        skewness  1.468308
9            stdv  0.403045
10  top1_repeated  0.000000
11  top2_repeated  1.000000
12        uniques  2.000000

**Puntos más relevantes:**
1.  La única variable numérica con la que estaremos trabajando es **`label`**.  Esta etiqueta tiene un valor de `1` cuando el código de cierre es `(F)`o `(N)` (la llamada es falsa), y `0` para cualquier otro caso (la llamada es verdadera).
2.  Se tiene un 20.41% de llamadas falsas (etiqueta `1`). 
3.  Se generaron etiquetas al 100% de los datos.

***Data profiling* de variables categóricas:**

In [120]:
def category_profiling(df, col):
    """
    Profiling for categoric columns. 
    
    :param: column to analyze
    :return: dictionary
    """
    profiling = {}

    profiling.update({'num_categories': df[col].nunique(),
                     'missings': df[col].isna().sum()/df[col].size*100,
                     'top1_repeated': get_repeated_values(df, col, 1),
                     'top2_repeated': get_repeated_values(df, col, 2),
                     'top3_repeated': get_repeated_values(df, col, 3)})
    
    return profiling

In [121]:
category_profiling_output = {elem: category_profiling(data, elem)\
                             for elem in category_variables}

category_profiling_output
df_category_profiling = pd.DataFrame(category_profiling_output).reset_index()
df_category_profiling.rename(columns={'index': 'metric'}, inplace=True)
df_category_profiling

metric hora_creacion dia_semana codigo_cierre  delegacion_inicio  \
0  num_categories        105887          7             5                 17   
1        missings             0          0             0                  0   
2   top1_repeated      20:44:00    Viernes             A         IZTAPALAPA   
3   top2_repeated      19:16:00     Sábado             D  GUSTAVO A. MADERO   
4   top3_repeated      18:38:00     Jueves             N         CUAUHTEMOC   

                      incidente_c4  clas_con_f_alarma      tipo_entrada  \
0                               26                  4                 9   
1                                0                  0                 0   
2  accidente-choque sin lesionados         EMERGENCIA   LLAMADA DEL 911   
3  accidente-choque con lesionados  URGENCIAS MEDICAS   LLAMADA DEL 066   
4            lesionado-atropellado       FALSA ALARMA  BOTÓN DE AUXILIO   

   delegacion_cierre año_creacion  mes_creacion  dia_creacion  \
0                 17            8          12.0          31.0   
1                  0            0           0.0           0.0   
2         IZTAPALAPA         2018          10.0          14.0   
3  GUSTAVO A. MADERO         2019           8.0          15.0   
4         CUAUHTEMOC         2017           9.0          13.0   

  mes_creacion_str hora_simple espacio_del_dia  
0               12          34               8  
1                0           0               0  
2          Octubre          19        6-8 p.m.  
3           Agosto          20        3-5 p.m.  
4       Septiembre          18       9-11 p.m.

**Puntos más relevantes:**

1.  No se cuenta con registros faltantes en las columnas categóricas.
2.  La delegación con más llamadas registradas es Iztapalapa, y el tipo de entrada más común es la "Llamada del 911".
3.  En cuanto a temporalidad, el mes con más registros es Octubre, el día de la semana con más registros es el Viernes, y el espacio del día con más registros es de 6 a 8pm.  

***Data profiling* de variables de fecha:**

In [122]:
def date_profiling(df, col):
    """
    Profiling for date columns. 
    
    :param: column to analyze
    :return: dictionary
    """
    profiling = {}

    profiling.update({'mode': df[col].mode().values,
                     'num_dates': df[col].nunique(),
                     'max': df[col].max(),
                     'min': df[col].min(),
                     'mean': df[col].mean(),
                     'uniques': df[col].nunique(),
                     'missings': df[col].isna().sum()/df[col].size*100,
                     'top1_repeated': get_repeated_values(df, col, 1),
                     'top2_repeated': get_repeated_values(df, col, 2),
                     'top3_repeated': get_repeated_values(df, col, 3)})
    
    return profiling

In [123]:
date_profiling_output = {elem: date_profiling(data, elem)\
                             for elem in date_variables}

In [124]:
date_profiling_output
df_date_profiling = pd.DataFrame(date_profiling_output).reset_index()
df_date_profiling.rename(columns={'index': 'metric'}, inplace=True)
df_date_profiling

metric                   fecha_creacion  \
0           mode  [2020-02-14T00:00:00.000000000]   
1      num_dates                             2497   
2            max              2020-10-31 00:00:00   
3            min              2013-12-31 00:00:00   
4           mean    2017-07-12 21:28:36.224410880   
5        uniques                             2497   
6       missings                                0   
7  top1_repeated              2020-02-14 00:00:00   
8  top2_repeated              2018-10-26 00:00:00   
9  top3_repeated              2017-12-08 00:00:00   

                      fecha_cierre  
0  [2020-02-14T00:00:00.000000000]  
1                             2496  
2              2020-10-31 00:00:00  
3              2014-01-01 00:00:00  
4    2017-07-12 23:02:39.774077952  
5                             2496  
6                                0  
7              2020-02-14 00:00:00  
8              2017-12-02 00:00:00  
9              2017-12-08 00:00:00

**Puntos más relevantes:**
1.  La información con la que contamos cubre los años 2014 - 2020.  Como los registros se reflejan en el sistema con un día de retraso, los registros con fecha de cierre 2014/01/01 fueron en realidad creados el 2013/12/31, siendo esta la fecha más lejana registrada.
2.  La fecha más reciente registrada es del 2020/10/31, que cuadra con la última fecha registrada en el número de folio.  Originalmente se habían encontrado errores en las fechas con meses y días invertidos, estos errores se solucionaron al agregar el arugmento **`dayfirst = True`** en nuestra función de transformación de fechas.  Nótese que ya no contamos con la columna `folio` para nuestro análisis.
3.  La fecha más repetida es el 14/Feb/2020.

***Data profiling* de variables geoespaciales:**

In [126]:
def geospace_profiling(df, col):
    """
    Profiling for geospace columns. 
    
    :param: column to analyze
    :return: dictionary
    """
    profiling = {}

    profiling.update({'mode': df[col].mode().values,
                     'max': df[col].max(),
                     'min': df[col].min(),
                     'mean': df[col].mean(),
                     'stdv': df[col].std(),
                     '25%': df[col].quantile(.25),
                     'median': df[col].median(),
                     '75%': df[col].quantile(.75),
                     'kurtosis': df[col].kurt(),
                     'skewness': df[col].skew(),
                     'uniques': df[col].nunique(),
                     'prop_missings': df[col].isna().sum()/df.shape[0]*100,
                     'top1_repeated': get_repeated_values(df, col, 1),
                     'top2_repeated': get_repeated_values(df, col, 2),})
    
    return profiling

In [127]:
profiling_dict = {}

geospace_profiling_output = {elem: geospace_profiling(data, elem)\
                            for elem in geospace_variables}

In [128]:
df_geospace_profiling = pd.DataFrame(geospace_profiling_output).reset_index()
df_geospace_profiling.rename(columns={'index': 'metric'}, inplace=True)
df_geospace_profiling

metric        latitud        longitud
0            mode  [19.30431996]  [-99.08024004]
1             max        195.303        -98.9454
2             min         19.094        -991.764
3            mean        19.3839        -99.1436
4            stdv       0.266638         2.39968
5             25%        19.3369        -99.1793
6          median        19.3841        -99.1402
7             75%         19.435         -99.096
8        kurtosis         400835          138084
9        skewness        611.376        -371.477
10        uniques          82501           78984
11  prop_missings      0.0320286       0.0314502
12  top1_repeated        19.3043        -99.0802
13  top2_repeated        19.3717        -99.0871

**Puntos más relevantes:**
1.  Originalmente se encontró aproximadamente un 3% de valores faltantes de latitud y longitud, que decidimos **decisión sobre datos geoespaciales faltantes**.  Una vez imputados estos valores, la información con la que trabajaremos no tiene valores faltantes.
2.  Se encontraron también errores de escritura tanto para latitud como longitud.  En el caso de la latitud, había **3** registros con valores de aproximadamente 190, cuando el promedio de la latitud es 19.09.  En el caso de la longitud, había **10** registros con un valor de aproximadamente -991, cuando el valor promedio es de -99.14.  Se decidió **decisión sobre datos geoespaciales erróneos**, eliminando estos valores incorrectos.
3.  El punto más repetido es (19.3043, -99.0802), con ubicación en **agregar ubicación de éste punto en el mapa**.

In [129]:
len(data[data["latitud"] > 19.9])

3

In [130]:
len(data[data["longitud"] < -99.9])

10

## Pendiente:
- Decisión para imputación de datos geoespaciales faltantes.
- Decisión sobre los datos geoespaciales erróneos (eliminarlos?  son sólo 13 registros).

## Agregando el mapa:

In [131]:
def generateBaseMap(default_location = [19.3841, -99.1402], default_zoom_start = 10):
    base_map = folium.Map(location = default_location, control_scale = True, zoom_start = default_zoom_start)
    return base_map

In [132]:
# Data frame con llamadas falsas:
data_false = pd.DataFrame(data[data["label"] == 1])

# Data frame con llamadas verdaderas:
data_true = pd.DataFrame(data[data["label"] == 0])
for row in ["label"]:
    data_true[row] = 1

In [133]:
from folium.plugins import HeatMap
from folium.plugins import FloatImage

base_map = generateBaseMap()

# Marcadores para punto con más registros, y más registros falsos:
folium.Marker([data["latitud"].mode(), data["longitud"].mode()], popup = "Punto con mas registros").add_to(base_map)
folium.Marker([data_false["latitud"].mode(), data_false["longitud"].mode()], popup = "Punto con mas registros falsos", icon=folium.Icon(color="red")).add_to(base_map)

#Mapas de calor para llamadas falsas y verdaderas:
HeatMap(data = data_true[['latitud', 'longitud', 'label']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist(), radius=8, max_zoom=13, blur = 17, gradient={.2: '#ececa3', .6:"#abc32f", 1: '#607c3c'}).add_to(base_map)
HeatMap(data = data_false[['latitud', 'longitud', 'label']].groupby(['latitud', 'longitud']).sum().reset_index().values.tolist(), radius=8, max_zoom=13, blur = 24, gradient={.2: '#ffbaba', .6:"#ff5252", 1: '#a70000'}).add_to(base_map)

#Agregando leyenda:
url = ('https://drive.google.com/file/d/1s2UD1S5vaMz4kxnTu2Y_ISN44U_-Alar/view?usp=sharing')
FloatImage(url, bottom = 90, left = 80).add_to(base_map)

In [134]:
base_map

## Pendiente:
- Arreglar imagen con leyenda.